In [1]:
# Libraries 
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
import tensorflow as tf
import tensorflow.keras as keras
import cv2
from PIL import Image
import os
from sklearn.metrics import classification_report
import time
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.optimizers import Adam

In [2]:
base_path = r"C:\Users\Lenovo\OneDrive\Compression\archive"
save_path = r".\trafficsignnet.model"
plot_path = r".\plot.png"
test_path = r".\Test"
example_path = r".\examples"

In [3]:
# Reading the input images and putting them into a numpy array
data=[]
labels=[]

height = 32
width = 32
channels = 1
classes = 43
n_inputs = height * width*channels
NUM_EPOCHS = 30
INIT_LR = 1e-3
BS = 64

for i in range(classes) :
    path = base_path+"/train/{0}/".format(i)
    print(path)
    Class=os.listdir(path)
    for a in Class:
        try:
            image=cv2.imread(path+a, cv2.IMREAD_GRAYSCALE)
#             print(image)
#             image_from_array = Image.fromarray(image, 'L')
            image = cv2.resize(image, (height, width))
            data.append(np.array(image))
#             print(image)
            labels.append(i)
        except AttributeError:
            print("Error")
#     print(data)
Cells=np.array(data)
labels=np.array(labels)

#Randomize the order of the input images
s=np.arange(Cells.shape[0])
np.random.seed(43)
np.random.shuffle(s)
Cells=Cells[s]
labels=labels[s]

C:\Users\Lenovo\OneDrive\Compression\archive/train/0/
C:\Users\Lenovo\OneDrive\Compression\archive/train/1/
C:\Users\Lenovo\OneDrive\Compression\archive/train/2/
C:\Users\Lenovo\OneDrive\Compression\archive/train/3/
C:\Users\Lenovo\OneDrive\Compression\archive/train/4/
C:\Users\Lenovo\OneDrive\Compression\archive/train/5/
C:\Users\Lenovo\OneDrive\Compression\archive/train/6/
C:\Users\Lenovo\OneDrive\Compression\archive/train/7/
C:\Users\Lenovo\OneDrive\Compression\archive/train/8/
C:\Users\Lenovo\OneDrive\Compression\archive/train/9/
C:\Users\Lenovo\OneDrive\Compression\archive/train/10/
C:\Users\Lenovo\OneDrive\Compression\archive/train/11/
C:\Users\Lenovo\OneDrive\Compression\archive/train/12/
C:\Users\Lenovo\OneDrive\Compression\archive/train/13/
C:\Users\Lenovo\OneDrive\Compression\archive/train/14/
C:\Users\Lenovo\OneDrive\Compression\archive/train/15/
C:\Users\Lenovo\OneDrive\Compression\archive/train/16/
C:\Users\Lenovo\OneDrive\Compression\archive/train/17/
C:\Users\Lenovo\OneD

In [4]:
#Spliting the images into train and validation sets
(X_train,X_val)=Cells[(int)(0.2*len(labels)):],Cells[:(int)(0.2*len(labels))]
X_train = X_train.astype('float32')/255 
X_val = X_val.astype('float32')/255
(y_train,y_val)=labels[(int)(0.2*len(labels)):],labels[:(int)(0.2*len(labels))]

#Using one hote encoding for the train and validation labels
from tensorflow.keras.utils import to_categorical
y_train = to_categorical(y_train, 43)
y_val = to_categorical(y_val, 43)

In [5]:
#accounting for the skewed classes
classTotals = y_train.sum(axis=0)
classWeight = dict()
# loop over all classes and calculate the class weight
for i in range(0, len(classTotals)):
    classWeight[i] = classTotals.max() / classTotals[i]

In [6]:
X_train.shape

(31368, 32, 32)

In [7]:
y_train.shape

(31368, 43)

In [8]:
X_train = X_train[:,:,:,np.newaxis]
X_val = X_val[:,:,:,np.newaxis]

In [10]:
X_train.shape

(31368, 32, 32, 1)

In [11]:
import matplotlib
matplotlib.use("Agg")
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.utils import to_categorical
from sklearn.metrics import classification_report
from skimage import transform
from skimage import exposure
from skimage import io
import matplotlib.pyplot as plt
import numpy as np
import argparse
import random
import os
import time
import cv2

In [12]:
#function to load the dataset from the csv.
def load(basePath, csvPath):
    
    data = []
    labels = []
    rows = open(csvPath).read().strip().split("\n")[1:]
    #shuffling rows to shuffle classes
    random.shuffle(rows)
    
    # loop over the rows
    for (i, row) in enumerate(rows):
        if i % 1000 == 0:
            print("[INFO] processed {} total images".format(i))
       
        #split each row
        (label, imagePath) = row.strip().split(",")[-2:]
        
        #load each path
        imagePath = os.path.sep.join([basePath, imagePath])
        print(imagePath)
        image = cv2.imread(imagePath,cv2.IMREAD_GRAYSCALE)
        
        # resize the image to be 32x32 pixels and 
        # applying Contrast Limited Adaptive Histogram Equalization (CLAHE)
        image = transform.resize(image, (32, 32))
        image = exposure.equalize_adapthist(image, clip_limit=0.1)
        data.append(image)
        labels.append(int(label))
        
    # convering to np array
    data = np.array(data)
    labels = np.array(labels)

    return (data, labels)

In [13]:
# derive training and testing CSV paths
trainPath = os.path.sep.join([base_path, "Train.csv"])
testPath = os.path.sep.join([base_path, "Test.csv"])
# print(trainPath)
# print(testPath)
# print(base_path)

# load the training and testing data
print("[INFO] loading training and testing data...")
(trainX, trainY) = load(base_path, trainPath)
(testX, testY) = load(base_path, testPath)

[INFO] loading training and testing data...
[INFO] processed 0 total images
C:\Users\Lenovo\OneDrive\Compression\archive\Train/4/00004_00022_00004.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/17/00017_00024_00009.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/13/00013_00057_00015.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/14/00014_00010_00009.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/10/00010_00040_00014.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/8/00008_00025_00024.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/13/00013_00056_00001.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00034_00014.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00056_00018.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/7/00007_00012_00015.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/10/00010_00015_00003.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/5/00005_00060_00000.png
C:\Users\Lenovo\On

C:\Users\Lenovo\OneDrive\Compression\archive\Train/38/00038_00006_00016.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/25/00025_00026_00012.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/26/00026_00011_00026.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/5/00005_00031_00029.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00072_00010.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/25/00025_00046_00015.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/4/00004_00017_00000.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/7/00007_00032_00014.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/8/00008_00003_00006.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/15/00015_00017_00003.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/1/00001_00016_00017.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/31/00031_00012_00023.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/36/00036_00004_00003.png
C:\Users\Lenovo\On

C:\Users\Lenovo\OneDrive\Compression\archive\Train/35/00035_00000_00027.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/11/00011_00025_00016.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/8/00008_00029_00020.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00052_00009.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00061_00001.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/7/00007_00042_00015.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/17/00017_00017_00007.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00046_00016.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/26/00026_00006_00001.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/17/00017_00010_00002.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/14/00014_00023_00016.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/35/00035_00033_00019.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/18/00018_00000_00013.png
C:\Users\Lenovo\O

C:\Users\Lenovo\OneDrive\Compression\archive\Train/28/00028_00001_00005.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/1/00001_00021_00016.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/5/00005_00020_00015.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/38/00038_00044_00023.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00039_00017.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/18/00018_00010_00018.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/5/00005_00049_00007.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/28/00028_00015_00018.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/14/00014_00004_00005.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/13/00013_00046_00028.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/2/00002_00010_00012.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/12/00012_00021_00018.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/4/00004_00040_00011.png
C:\Users\Lenovo\On

C:\Users\Lenovo\OneDrive\Compression\archive\Train/10/00010_00065_00013.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/38/00038_00028_00025.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/6/00006_00010_00004.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/1/00001_00041_00015.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/4/00004_00043_00009.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/9/00009_00015_00014.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/38/00038_00016_00011.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/39/00039_00009_00008.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/36/00036_00005_00013.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/4/00004_00061_00029.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/1/00001_00000_00026.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/13/00013_00049_00022.png
C:\Users\Lenovo\OneDrive\Compression\archive\Train/41/00041_00000_00021.png
C:\Users\Lenovo\On

...

C:\Users\Lenovo\OneDrive\Compression\archive\Test/06551.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07820.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/06260.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10285.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07361.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/05025.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/04118.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/08088.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/06117.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11961.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/04156.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11946.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/08053.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/05944.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/05232.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/03478.png
C:\Users\Lenovo\OneDrive\Compression\arc

C:\Users\Lenovo\OneDrive\Compression\archive\Test/00959.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/00394.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/06116.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/12160.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10441.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/02542.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07789.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07326.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11864.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/09812.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01660.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10497.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01525.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/00271.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11447.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10234.png
C:\Users\Lenovo\OneDrive\Compression\arc

C:\Users\Lenovo\OneDrive\Compression\archive\Test/08455.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/08695.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/03728.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/02929.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01776.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11412.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10217.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/04614.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01355.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10848.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07067.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/06205.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/05274.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/04381.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01104.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01378.png
C:\Users\Lenovo\OneDrive\Compression\arc

C:\Users\Lenovo\OneDrive\Compression\archive\Test/00813.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10981.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10752.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01342.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/03822.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/02455.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/04797.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/06045.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/10008.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/09814.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/09806.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/05209.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/00063.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11852.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01070.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11926.png
C:\Users\Lenovo\OneDrive\Compression\arc

C:\Users\Lenovo\OneDrive\Compression\archive\Test/10569.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/09797.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/11246.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01498.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/00013.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01841.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/12018.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/12045.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07289.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/03358.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/04229.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07476.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/01354.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/03315.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/06218.png
C:\Users\Lenovo\OneDrive\Compression\archive\Test/07692.png
C:\Users\Lenovo\OneDrive\Compression\arc

In [14]:
trainX.shape

(39209, 32, 32)

In [15]:
trainY.shape

(39209,)

In [16]:
trainX = trainX[:,:,:,np.newaxis]

In [17]:
trainX.shape

(39209, 32, 32, 1)

In [18]:
import tensorflow_model_optimization as tfmot
import numpy as np
import tensorflow as tf
import tempfile

In [32]:
loaded_model = tf.keras.models.load_model(save_path+r"\20220117-180435.hdf")

In [33]:
prune_low_magnitude = tfmot.sparsity.keras.prune_low_magnitude

In [34]:
batch_size = 32
epochs = 2
validation_split = 0.1

In [35]:
num_images = 10360 * (1 - validation_split)
end_step = np.ceil(num_images / batch_size).astype(np.int32) * epochs

In [36]:
pruning_params = {
      'pruning_schedule': tfmot.sparsity.keras.PolynomialDecay(initial_sparsity=0.50,
                                                               final_sparsity=0.80,
                                                               begin_step=0,
                                                               end_step=end_step)
}

In [37]:
model_for_pruning = prune_low_magnitude(loaded_model, **pruning_params)

In [38]:
model_for_pruning.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

In [39]:
model_for_pruning.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 prune_low_magnitude_conv2d   (None, 28, 28, 32)       1634      
 (PruneLowMagnitude)                                             
                                                                 
 prune_low_magnitude_conv2d_  (None, 26, 26, 64)       36930     
 1 (PruneLowMagnitude)                                           
                                                                 
 prune_low_magnitude_max_poo  (None, 13, 13, 64)       1         
 ling2d (PruneLowMagnitude)                                      
                                                                 
 prune_low_magnitude_dropout  (None, 13, 13, 64)       1         
  (PruneLowMagnitude)                                            
                                                                 
 prune_low_magnitude_conv2d_  (None, 11, 11, 64)       7

In [40]:
logdir = tempfile.mkdtemp()

callbacks = [
  tfmot.sparsity.keras.UpdatePruningStep(),
  tfmot.sparsity.keras.PruningSummaries(log_dir=logdir),
]

model_for_pruning.fit(trainX, trainY,
                  batch_size=batch_size, epochs=epochs, validation_split=validation_split,
                  callbacks=callbacks)

Epoch 1/2
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing th

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
1103/1103 [==============================] - 65s 55ms/step - loss: 

In [41]:
testX.shape

(12630, 32, 32)

In [42]:
testY.shape

(12630,)

In [43]:
_, model_for_pruning_accuracy = model_for_pruning.evaluate(
   testX, testY, verbose=0)

#print('Baseline test accuracy:', baseline_model_accuracy) 
print('Pruned test accuracy:', model_for_pruning_accuracy)

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Pruned test accuracy: 0.9724465608596802


In [44]:
model_for_export = tfmot.sparsity.keras.strip_pruning(model_for_pruning)

_, pruned_keras_file = tempfile.mkstemp('.h5')
tf.keras.models.save_model(model_for_export, pruned_keras_file, include_optimizer=False)
print('Saved pruned Keras model to:', pruned_keras_file)

Saved pruned Keras model to: C:\Users\Lenovo\AppData\Local\Temp\tmpnixul613.h5


In [45]:
converter = tf.lite.TFLiteConverter.from_keras_model(model_for_export)
pruned_tflite_model = converter.convert()

_, pruned_tflite_file = tempfile.mkstemp('.tflite')

with open(pruned_tflite_file, 'wb') as f:
  f.write(pruned_tflite_model)

print('Saved pruned TFLite model to:', pruned_tflite_file)

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Constant'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Constant'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity t

Saved pruned TFLite model to: C:\Users\Lenovo\AppData\Local\Temp\tmpzw2x3d9c.tflite


In [46]:
def get_gzipped_model_size(file):
  # Returns size of gzipped model, in bytes.
    import os
    import zipfile

    _, zipped_file = tempfile.mkstemp('.zip')
    with zipfile.ZipFile(zipped_file, 'w', compression=zipfile.ZIP_DEFLATED) as f:
        f.write(file)

    return os.path.getsize(zipped_file)

In [47]:
#print("Size of gzipped baseline Keras model: %.2f bytes" % (get_gzipped_model_size(keras_file)))
print("Size of gzipped pruned Keras model: %.2f bytes" % (get_gzipped_model_size(pruned_keras_file)))
print("Size of gzipped pruned TFlite model: %.2f bytes" % (get_gzipped_model_size(pruned_tflite_file)))

Size of gzipped pruned Keras model: 572813.00 bytes
Size of gzipped pruned TFlite model: 563425.00 bytes


# Create a 10x smaller model from combining pruning and quantization

In [48]:
converter = tf.lite.TFLiteConverter.from_keras_model(model_for_export)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
quantized_and_pruned_tflite_model = converter.convert()

_, quantized_and_pruned_tflite_file = tempfile.mkstemp('.tflite')

with open(quantized_and_pruned_tflite_file, 'wb') as f:
  f.write(quantized_and_pruned_tflite_model)

print('Saved quantized and pruned TFLite model to:', quantized_and_pruned_tflite_file)

print("Size of gzipped only pruned Keras model: %.2f bytes" % (get_gzipped_model_size(pruned_keras_file)))
print("Size of gzipped pruned and quantized TFlite model: %.2f bytes" % (get_gzipped_model_size(quantized_and_pruned_tflite_file)))

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Constant'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Constant'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Constant'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
INFO:tensorflow:Assets written to: C:\Users\Lenovo\AppData\Local\Temp\tmpw9n055h6\assets


INFO:tensorflow:Assets written to: C:\Users\Lenovo\AppData\Local\Temp\tmpw9n055h6\assets


Saved quantized and pruned TFLite model to: C:\Users\Lenovo\AppData\Local\Temp\tmp3e667geo.tflite
Size of gzipped only pruned Keras model: 572813.00 bytes
Size of gzipped pruned and quantized TFlite model: 164185.00 bytes


In [51]:
testX.shape

(12630, 32, 32, 1)

In [50]:
testX = np.expand_dims(testX, axis = 3)

In [53]:
import numpy as np

def evaluate_model(interpreter):
    input_index = interpreter.get_input_details()[0]["index"]
    #print(interpreter.get_input_details())
    output_index = interpreter.get_output_details()[0]["index"]
    
  # Run predictions on ever y image in the "test" dataset.
    prediction_digits = []
    for i, test in enumerate(testX):
        if i % 1000 == 0:
            print('Evaluated on {n} results so far.'.format(n=i))
    # Pre-processing: add batch dimension and convert to float32 to match with
    # the model's input data format.
        test = np.expand_dims(test, axis=0).astype(np.float32)
        interpreter.set_tensor(input_index, test)

    # Run inference.
        interpreter.invoke()

    # Post-processing: remove batch dimension and find the digit with highest
    # probability.
        output = interpreter.tensor(output_index)
        digit = np.argmax(output()[0])
        prediction_digits.append(digit)

    print('\n')
  # Compare prediction results with ground truth labels to calculate accuracy.
    prediction_digits = np.array(prediction_digits)
    accuracy = (prediction_digits == testY).mean()
    return accuracy

In [54]:
interpreter = tf.lite.Interpreter(model_content=quantized_and_pruned_tflite_model)
interpreter.allocate_tensors()

test_accuracy = evaluate_model(interpreter)

print('Pruned and quantized TFLite test_accuracy:', test_accuracy)
print('Pruned TF test accuracy:', model_for_pruning_accuracy)

Evaluated on 0 results so far.
Evaluated on 1000 results so far.
Evaluated on 2000 results so far.
Evaluated on 3000 results so far.
Evaluated on 4000 results so far.
Evaluated on 5000 results so far.
Evaluated on 6000 results so far.
Evaluated on 7000 results so far.
Evaluated on 8000 results so far.
Evaluated on 9000 results so far.
Evaluated on 10000 results so far.
Evaluated on 11000 results so far.
Evaluated on 12000 results so far.


Pruned and quantized TFLite test_accuracy: 0.9726049089469517
Pruned TF test accuracy: 0.9724465608596802
